In [24]:
import numpy as np
import pandas as pd
from pycaret.clustering import *
import pycaret
import dataprep.eda as eda 
from dataprep.eda import create_report
import os

In [67]:
os.chdir(r'C:\Users\kevinp\Videos\KP\Power BI (DataLatam)\Data')
df_AW = pd.read_csv('Adventure Works 2020 Kmeans.csv', sep = ';', decimal = ',')
df_AW['OrderDate'] = pd.to_datetime(df_AW['OrderDate'], dayfirst = True, format = '%d/%m/%Y')
df_AW['OrderDate_Year'] = df_AW['OrderDate'].dt.year
df_AW['OrderDate_Month'] = df_AW['OrderDate'].dt.month
df_AW = df_AW[['OrderDate_Year', 'OrderDate_Month', 'CustomerKey', 'OrderQuantity', 'SalesAmount', 'SalesOrderNumber', 'SubCategory']]

In [68]:
df_AW = df_AW.groupby(['OrderDate_Year', 'OrderDate_Month', 'CustomerKey']).agg(
    Cantidad_Total_Productos = ('OrderQuantity', sum),
    Compra_Total = ('SalesAmount', sum),
    Cantidad_Compras = ('SalesOrderNumber', 'count'),
    Total_Subcategorias_Compradas = ('SubCategory', 'count') 
).reset_index()
df_AW['Q_Productos_Compra'] = df_AW['Cantidad_Total_Productos'] / df_AW['Cantidad_Compras']
df_AW['Ticket_Compra'] = df_AW['Compra_Total'] / df_AW['Cantidad_Compras']

In [69]:
df_AW

OrderDate_Year  OrderDate_Month  CustomerKey  Cantidad_Total_Productos  \
0                2016                7        11000                         1   
1                2016                7        11001                         1   
2                2016                7        11002                         1   
3                2016                7        11003                         1   
4                2016                7        11004                         1   
...               ...              ...          ...                       ...   
26933            2019                7        29262                        15   
26934            2019                7        29282                        16   
26935            2019                7        29288                         9   
26936            2019                7        29305                         8   
26937            2019                7        29471                        12   

       Compra_Total  Cantidad_Compras  Total_Subcategorias_Compradas  \
0           3399.99                 1                              1   
1           3374.99                 1                              1   
2           3399.99                 1                              1   
3           3399.99                 1                              1   
4           3399.99                 1                              1   
...             ...               ...                            ...   
26933        306.85                 3                              3   
26934        124.84                 3                              3   
26935        269.91                 2                              2   
26936         59.92                 2                              2   
26937        142.68                 2                              2   

       Q_Productos_Compra  Ticket_Compra  
0                1.000000    3399.990000  
1                1.000000    3374.990000  
2                1.000000    3399.990000  
3                1.000000    3399.990000  
4                1.000000    3399.990000  
...                   ...            ...  
26933            5.000000     102.283333  
26934            5.333333      41.613333  
26935            4.500000     134.955000  
26936            4.000000      29.960000  
26937            6.000000      71.340000  

[26938 rows x 9 columns]

In [73]:
os.chdir(r'C:\Users\kevinp\OneDrive - MARCO Marketing\Marco MKT\IA\Cluster Kmeans')
df_AW.to_csv('Base_Clientes.csv', index=False, sep = ';', decimal = ',')

In [28]:
df_AW.columns

Index(['OrderDate_Year', 'OrderDate_Month', 'CustomerKey',
       'Cantidad_Total_Productos', 'Compra_Total', 'Cantidad_Compras',
       'Total_Subcategorias_Compradas', 'Q_Productos_Compra', 'Ticket_Compra'],
      dtype='object')

In [38]:
clustering_1 = setup(
    data = df_AW,
    normalize = True,
    session_id = 150,
    ignore_features = ['OrderDate_Year', 'OrderDate_Month', 'CustomerKey']
) 
# Es importante normalizar los datos.
# Esta función inicializa el entorno de entrenamiento y crea la canalización de transformación. La función de configuración debe llamarse antes de ejecutar cualquier otra función. 
# Toma un parámetro obligatorio: DATA. Todos los demás parámetros son opcionales.

In [30]:
models() # Lista todos los modelos de clusterización disponibles

Name  \
ID                                            
kmeans                   K-Means Clustering   
ap                     Affinity Propagation   
meanshift             Mean Shift Clustering   
sc                      Spectral Clustering   
hclust             Agglomerative Clustering   
dbscan     Density-Based Spatial Clustering   
optics                    OPTICS Clustering   
birch                      Birch Clustering   

                                                   Reference  
ID                                                            
kmeans                        sklearn.cluster._kmeans.KMeans  
ap         sklearn.cluster._affinity_propagation.Affinity...  
meanshift              sklearn.cluster._mean_shift.MeanShift  
sc              sklearn.cluster._spectral.SpectralClustering  
hclust     sklearn.cluster._agglomerative.AgglomerativeCl...  
dbscan                        sklearn.cluster._dbscan.DBSCAN  
optics                        sklearn.cluster._optics.OPTICS  
birch                           sklearn.cluster._birch.Birch

## Compare models:
Esta función entrena y evalúa el rendimiento de todos los estimadores disponibles en la biblioteca de modelos mediante validación cruzada. El resultado de esta función es una cuadrícula de puntuación con puntuaciones medias validadas de forma cruzada. Se puede acceder a las métricas evaluadas durante CV mediante la función get_metrics. Las métricas personalizadas se pueden agregar o eliminar mediante las funciones add_metric y remove_metric.

PARA EL CASO DE CLUSTER, NO SE ENCUENTRA LA FUNCIÓN COMPARE_MODELS.

In [31]:
kmeans_model = create_model('kmeans') # Modelo generico para verificar el # de clusteres ideal que represente el puntaje de distorción optimo vs # clusteres:

In [32]:
evaluate_model(kmeans_model) # Codo en k = 5, es decir, punto optimo.

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Pipeline Plot', 'pipelin…

In [45]:
kmeans_model = create_model('kmeans', num_clusters = 5) # Ajustar el modelo k-means con el # de clusters optimo, es decir, k = 5.

In [49]:
df_AW_result = assign_model(kmeans_model)
df_AW_result.head(5)

Cantidad_Total_Productos  Compra_Total  Cantidad_Compras  \
0                         1    3399.98999                 1   
1                         1    3374.98999                 1   
2                         1    3399.98999                 1   
3                         1    3399.98999                 1   
4                         1    3399.98999                 1   

   Total_Subcategorias_Compradas  Q_Productos_Compra  Ticket_Compra    Cluster  
0                              1                 1.0     3399.98999  Cluster 4  
1                              1                 1.0     3374.98999  Cluster 4  
2                              1                 1.0     3399.98999  Cluster 4  
3                              1                 1.0     3399.98999  Cluster 4  
4                              1                 1.0     3399.98999  Cluster 4

In [50]:
os.chdir(r'C:\Users\kevinp\OneDrive - MARCO Marketing\Marco MKT\IA\Cluster Kmeans\Datos')
df_AW_result.to_csv('Clientes.csv', index=False)

In [51]:
save_model(kmeans_model, 'Saved_Kmeans_Model')

Transformation Pipeline and Model Successfully Saved


(Pipeline(memory=Memory(location=C:\Users\kevinp\AppData\Local\Temp\joblib),
          steps=[('numerical_imputer',
                  TransformerWrapper(include=['Cantidad_Total_Productos',
                                              'Compra_Total', 'Cantidad_Compras',
                                              'Total_Subcategorias_Compradas',
                                              'Q_Productos_Compra',
                                              'Ticket_Compra'],
                                     transformer=SimpleImputer())),
                 ('categorical_imputer',
                  TransformerWrapper(include=[],
                                     transformer=SimpleImputer(strategy='most_frequent'))),
                 ('normalize', TransformerWrapper(transformer=StandardScaler())),
                 ('trained_model', KMeans(n_clusters=5, random_state=150))]),
 'Saved_Kmeans_Model.pkl')

## Carga de modelo y NUEVO ajuste:

In [56]:
carga_datos = pd.read_csv('Clientes.csv', sep = ',', decimal = '.')
carga_datos = carga_datos.iloc[:, 0:6].reset_index(drop = True)
carga_datos.dtypes

Cantidad_Total_Productos           int64
Compra_Total                     float64
Cantidad_Compras                   int64
Total_Subcategorias_Compradas      int64
Q_Productos_Compra               float64
Ticket_Compra                    float64
dtype: object

In [58]:
carga_modelo = load_model(r'C:\Users\kevinp\OneDrive - MARCO Marketing\Marco MKT\IA\Cluster Kmeans\Datos\Saved_Kmeans_Model')
print(carga_modelo)

Transformation Pipeline and Model Successfully Loaded
Pipeline(memory=Memory(location=C:\Users\kevinp\AppData\Local\Temp\joblib),
         steps=[('numerical_imputer',
                 TransformerWrapper(include=['Cantidad_Total_Productos',
                                             'Compra_Total', 'Cantidad_Compras',
                                             'Total_Subcategorias_Compradas',
                                             'Q_Productos_Compra',
                                             'Ticket_Compra'],
                                    transformer=SimpleImputer())),
                ('categorical_imputer',
                 TransformerWrapper(include=[],
                                    transformer=SimpleImputer(strategy='most_frequent'))),
                ('normalize', TransformerWrapper(transformer=StandardScaler())),
                ('trained_model', KMeans(n_clusters=5, random_state=150))])


In [119]:
df_carga = pycaret.clustering.predict_model(model = carga_modelo, data = carga_datos)

In [142]:
df_carga.head(5)

Cantidad_Total_Productos Compra_Total  Cantidad_Compras  \
0                         1      3399,99                 1   
1                         1      3374,99                 1   
2                         1      3399,99                 1   
3                         1      3399,99                 1   
4                         1      3399,99                 1   

   Total_Subcategorias_Compradas  Q_Productos_Compra Ticket_Compra    Cluster  
0                              1                 1.0       3399.99  Cluster 4  
1                              1                 1.0       3374.99  Cluster 4  
2                              1                 1.0       3399.99  Cluster 4  
3                              1                 1.0       3399.99  Cluster 4  
4                              1                 1.0       3399.99  Cluster 4

## Cambiar el tipo de datos y posteriormente cambiar el separador de decimal para que sea valido en Power BI:

In [143]:
df_carga = df_carga.astype({'Compra_Total': str, 'Ticket_Compra': str})

In [145]:
df_carga['Compra_Total'] = df_carga['Compra_Total'].str.replace('.', ',')
df_carga['Ticket_Compra'] = df_carga['Ticket_Compra'].str.replace('.', ',')

In [146]:
df_carga

Cantidad_Total_Productos Compra_Total  Cantidad_Compras  \
0                             1      3399,99                 1   
1                             1      3374,99                 1   
2                             1      3399,99                 1   
3                             1      3399,99                 1   
4                             1      3399,99                 1   
...                         ...          ...               ...   
26933                        15       306,85                 3   
26934                        16       124,84                 3   
26935                         9       269,91                 2   
26936                         8        59,92                 2   
26937                        12       142,68                 2   

       Total_Subcategorias_Compradas  Q_Productos_Compra Ticket_Compra  \
0                                  1            1.000000       3399,99   
1                                  1            1.000000       3374,99   
2                                  1            1.000000       3399,99   
3                                  1            1.000000       3399,99   
4                                  1            1.000000       3399,99   
...                              ...                 ...           ...   
26933                              3            5.000000     102,28333   
26934                              3            5.333333     41,613335   
26935                              2            4.500000       134,955   
26936                              2            4.000000         29,96   
26937                              2            6.000000         71,34   

         Cluster  
0      Cluster 4  
1      Cluster 4  
2      Cluster 4  
3      Cluster 4  
4      Cluster 4  
...          ...  
26933  Cluster 3  
26934  Cluster 3  
26935  Cluster 0  
26936  Cluster 0  
26937  Cluster 0  

[26938 rows x 7 columns]